In [1]:
//If using Almond dependency
import $ivy.`org.vegas-viz::vegas:0.3.11`

import $ivy.$                            

In [ ]:
//If using Apache Toree dependency
%AddDeps org.vegas-viz vegas_2.11 0.3.11 --transitive

In [ ]:
//If using Apache Toree dependency
implicit val render = vegas.render.ShowHTML(kernel.display.content("text/html", _))

# Data Exploration with Functional Programming using Jupyter Notebook, Scala and Vegas
## A Statistical Analysis of the Titanic Dataset

Titanic survivor dataset captures the various details of people who survived or not survived in the shipwreck. Using this data, we want to build a model which predicts the propability of someone's survival. It is a classification problem that maps all attributes like sex, fare, age on the most probable state: Survived or not

![Titanic](Titanic.jpg)
(Source: https://commons.wikimedia.org/wiki/RMS_Titanic)


The dataset contains the following attributes (for more information: see Kaggle):

| **Variable** | **Definition**                                | **Key**                                           |
|--------------|-----------------------------------------------|---------------------------------------------------|
| survival     | Survival                                      | 1=Yes, 0= No                                      |
| pclass       | Ticket class                                  | 1 = 1st, 2 = 2nd, 3 = 3rd                         |
| sex          | Sex                                           |                                                   |
| age          | Age                                           | Age in years                                      |
| sibsp        |  # of siblings / spouses aboard   the Titanic |                                                   |
| parch        |  # of parents / children aboard   the Titanic |                                                   |
| ticket       | Ticket number                                 |                                                   |
| fare         | Passenger fare                                |                                                   |
| cabin        | Cabin number                                  |                                                   |
| embarked     | Port of Embarkation                           |  C = Cherbourg, Q = Queenstown,   S = Southampton |


The dataset is splittet into three files:
* A Training Dataset (train.csv)
* A Test Dataset (test.csv)
* A Set which contains sample data for the submission (gender_submission.csv).

At first, we need to load the data creating maps for each set.

In [2]:
import vegas._
import vegas.data.External._
import java.io.PrintWriter
import scala.util.Try

// Regular Expressions for extracting the information
val DATA_ACCESS_PATTERN_test = """(\d+),(\d),"(.+)",(male|female),([0-9]*\.[0-9]+|[0-9]+|d*),(\d*),(\d*),(.*),([0-9]*\.[0-9]+|[0-9]+|d*),(.*),(\w*)""".r
val DATA_ACCESS_PATTERN_train=  """(\d+),(\d),(\d),"(.+)",(male|female),([0-9]*\.[0-9]+|[0-9]+|d*),(\d*),(\d*),(.*),([0-9]*\.[0-9]+|[0-9]+|d*),(.*),(\w*)""".r

// Reading text file
// Stores the information in a map consisting of a property name (key) and its value
def loadDataCSV(filename:String):List[Map[String,Any]]= {

  val src = scala.io.Source.fromFile(filename)
  val iter = src.getLines().drop(1) //skip first line (property names)
    
    val result= (for (row <- iter) yield readData(row)).toList
   
    src.close
    result.flatMap(_ match{ case p:Option[Map[String,Any]]=>p})
}
  

// Extracting all information storing it into a Map[String,Any]
def readData(line:String):Option[Map[String,Any]]={
    
    def toInt(key: String, s: String): Option[(String, Int)] = Try(s.toInt).toOption.map((key, _))

    def toFloat(key: String, s: String): Option[(String, Float)] = Try(s.toFloat).toOption.map((key, _))
  
    def toString(key:String, s:String):Option[(String,String)]=
        if (s.nonEmpty) Some((key,s)) else None

    def createPassengerMap(t1:String,t2:String,t3:String,t4:String,t5:String,t6:String,t7:String,
                           t8:String,t9:String,t10:String,t11:String,t12:String):Option[Map[String,Any]]={
        
        val l=List(
            toInt("passengerID",t1),
            toInt("survived",t2),
            toInt("pclass",t3),
            toString("name",t4),
            toString("sex",t5),
            toFloat("age",t6),
            toInt("sibsp",t7),
            toInt("parch",t8),
            toString("ticket",t9),
            toFloat("fare",t10),
            toString("cabin",t11),
            {if (t12.length>0) Some(("embarked",t12(0))) else None})
         Some(l.flatMap(_ match{ case p:Option[(String,Any)]=>p}).toMap)        
    }
    
    val result = line match{
       case DATA_ACCESS_PATTERN_test(t1,t3,t4,t5,t6,t7,t8,t9,t10,t11,t12) => 
                 createPassengerMap(t1,"-1",t3,t4,t5,t6,t7,t8,t9,t10,t11,t12)
       
       case DATA_ACCESS_PATTERN_train(t1,t2,t3,t4,t5,t6,t7,t8,t9,t10,t11,t12) => {
                  createPassengerMap(t1,t2,t3,t4,t5,t6,t7,t8,t9,t10,t11,t12)
       }
       
     }
     result
}

// Method for printing a passenger in a readable manner
def printPassenger(p:Map[String,Any]):Unit={
    
    println("\n---------------------------------------------------------------------")
    println("passengerID:"+p.getOrElse("passengerID",-1))
    println("survived:"+p.getOrElse("survived",-1))
    println("pclass:"+p.getOrElse("pclass",-1))
    println("name:"+p.getOrElse("name","-"))
    println("sex:"+p.getOrElse("sex","-"))
    println("age:"+p.getOrElse("age",-1))
    println("sibsp:"+p.getOrElse("sibsp",-1))
    println("parch:"+p.getOrElse("parch",-1))
    println("ticket:"+p.getOrElse("ticket","-"))
    println("fare:"+p.getOrElse("fare",-1))
    println("cabin:"+p.getOrElse("cabin",-1))
    println("embarked:"+p.getOrElse("embarked",'-'))
    println("---------------------------------------------------------------------\n")
}
  
//produces sometimes an missing argument list error - can be ignored
def applyModel[CLASS,ID](model:(Map[String,Any],String)=> (ID,CLASS), 
            testdata: Seq[Map[String,Any]], idKey:String):Seq[(ID,CLASS)]= {
    
    testdata.map(d => model(d,idKey))
}  

def createSubmitFile[ID,CLASS](filename:String, data:Seq[(ID,CLASS)],header:String):Unit= {
    val pw = new PrintWriter(filename)
    pw.println(header)
    data.foreach(e=>pw.println(e._1.toString+","+e._2.toString))
    pw.close
}

import vegas._

import vegas.data.External._

import java.io.PrintWriter

import scala.util.Try

// Regular Expressions for extracting the information

DATA_ACCESS_PATTERN_test: scala.util.matching.Regex = (\d+),(\d),"(.+)",(male|female),([0-9]*\.[0-9]+|[0-9]+|d*),(\d*),(\d*),(.*),([0-9]*\.[0-9]+|[0-9]+|d*),(.*),(\w*)
DATA_ACCESS_PATTERN_train: scala.util.matching.Regex = (\d+),(\d),(\d),"(.+)",(male|female),([0-9]*\.[0-9]+|[0-9]+|d*),(\d*),(\d*),(.*),([0-9]*\.[0-9]+|[0-9]+|d*),(.*),(\w*)
defined function loadDataCSV
defined function readData
defined function printPassenger
defined function applyModel
defined function createSubmitFile

In [3]:
val train= loadDataCSV("train.csv")
val test= loadDataCSV("test.csv")
val all= train ++ test
  
println("Train Dataset:"+ train.size+" Elements")
println("Test Dataset:"+ test.size+" Elements")
println("Whole Dataset:"+ all.size+" Elements")

Train Dataset:891 Elements
Test Dataset:418 Elements
Whole Dataset:1309 Elements


train: List[Map[String, Any]] = List(
  Map(
    "name" -> "Braund, Mr. Owen Harris",
    "fare" -> 7.25F,
    "parch" -> 0,
    "age" -> 22.0F,
    "ticket" -> "A/5 21171",
    "sex" -> "male",
    "passengerID" -> 1,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "name" -> "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
    "fare" -> 71.2833F,
    "parch" -> 0,
    "age" -> 38.0F,
    "ticket" -> "PC 17599",
    "cabin" -> "C85",
    "sex" -> "female",
    "passengerID" -> 2,
    "pclass" -> 1,
    "sibsp" -> 1,
    "embarked" -> 'C',
    "survived" -> 1
  ),
  Map(
    "name" -> "Heikkinen, Miss. Laina",
    "fare" -> 7.925F,
    "parch" -> 0,
    "age" -> 26.0F,
    "ticket" -> "STON/O2. 3101282",
    "sex" -> "female",
    "passengerID" -> 3,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'S',
...
test: List[Map[String, Any]] = List(
  Map(
    "name" -> "Kelly, Mr. James",
    "fare" -> 7.8292F,
    "parch" -> 0,
   

Now we can examine a small sample of the data set

In [4]:
all.take(2).foreach(printPassenger)


---------------------------------------------------------------------
passengerID:1
survived:0
pclass:3
name:Braund, Mr. Owen Harris
sex:male
age:22.0
sibsp:1
parch:0
ticket:A/5 21171
fare:7.25
cabin:-1
embarked:S
---------------------------------------------------------------------


---------------------------------------------------------------------
passengerID:2
survived:1
pclass:1
name:Cumings, Mrs. John Bradley (Florence Briggs Thayer)
sex:female
age:38.0
sibsp:1
parch:0
ticket:PC 17599
fare:71.2833
cabin:C85
embarked:C
---------------------------------------------------------------------



Count the missing values in a passenger set.

In [5]:
val attList= List("passengerID","pclass","survived","name","sex","age","sibsp","parch",
        "ticket","fare","cabin","embarked")


def countAllMissingValues(data:List[Map[String,Any]],attList:List[String]):Map[String,Int] = {
  attList.map(att => (att,0)).toMap.
    map(x => (x._1, data.count(passenger => passenger.get(x._1).isEmpty)))
}


val train_mv = countAllMissingValues(train,attList)
print(train_mv)
val test_mv= countAllMissingValues(test,attList)
assert(train_mv("cabin")== 687 && train_mv("age")==177 && train_mv("embarked")== 2)
assert(test_mv("cabin")== 327 && test_mv("age")==86 && test_mv("fare")== 1)

Map(name -> 0, fare -> 0, parch -> 0, age -> 177, ticket -> 0, cabin -> 687, sex -> 0, passengerID -> 0, pclass -> 0, sibsp -> 0, embarked -> 2, survived -> 0)

attList: List[String] = List(
  "passengerID",
  "pclass",
  "survived",
  "name",
  "sex",
  "age",
  "sibsp",
  "parch",
  "ticket",
  "fare",
  "cabin",
  "embarked"
)
defined function countAllMissingValues
train_mv: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 0,
  "parch" -> 0,
  "age" -> 177,
  "ticket" -> 0,
  "cabin" -> 687,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 2,
  "survived" -> 0
)
test_mv: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 1,
  "parch" -> 0,
  "age" -> 86,
  "ticket" -> 0,
  "cabin" -> 327,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 0,
  "survived" -> 0
)

# DATA VISUALISATION

In [6]:
Vegas("Passengers split by sex" ).
    withData(train).
    mark(Bar).
    encodeX("sex", Ordinal,axis=Axis(title="Sex")).
    encodeY("passengerID", Quantitative,AggOps.Count,axis=Axis(title="Passengers")).
    show

<iframe id="frame-vegas-149df422-df2b-4ff4-963f-772e74058352" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-149df422-df2b-4ff4-963f-772e74058352'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "axis" : {
 "title" : "Sex"
 },
 "field" : "sex",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 }
 },
 "description" : "Passengers split by sex",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Saundercock, Mr. William Henry",
 "f

In [7]:
val passengers= train.size
val survivedPass= (train.filter(m=>m("survived")==1)).size
val rate= survivedPass.toDouble/passengers
println("propability of surviving:"+rate)

Vegas("Passengers classified by survival" ).
    withData(train).
    mark(Bar).
    addTransform("survival", "datum.survived == 0 ? \"Dead\" : \"Alive\"").
    encodeX("survival", Ordinal,axis=Axis(title="Survival")).
    encodeY("passengerID", Quantitative,AggOps.Count,axis=Axis(title="Passengers")).show

propability of surviving:0.3838383838383838


<iframe id="frame-vegas-6c3ceb7d-fe64-4d9b-8239-d0cc1c8551c9" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-6c3ceb7d-fe64-4d9b-8239-d0cc1c8551c9'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "axis" : {
 "title" : "Survival"
 },
 "field" : "survival",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 }
 },
 "description" : "Passengers classified by survival",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Saundercock, Mr.

passengers: Int = 891
survivedPass: Int = 342
rate: Double = 0.3838383838383838

In [8]:
Vegas("Survival split by sex").
      withData(train).
      mark(Bar).
      addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
      encodeY("passengerID",Quantitative, AggOps.Count, axis=Axis(title="Passengers")).
      encodeX("sex", Ord).
      encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
      show

<iframe id="frame-vegas-18d0de98-0f36-4d12-9ad2-c0b560ef3b5e" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-18d0de98-0f36-4d12-9ad2-c0b560ef3b5e'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "sex",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Survival split by sex",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sibsp" : 0,
 "embark

In [9]:
Vegas("Age Distribution of all Passengers").
    withData(train).
    mark(Bar).
    addTransformCalculation("age","datum.age-(datum.age % 10)").
    encodeX("age", dataType= Nominal,scale=Scale(bandSize=20.0)).
    encodeY("passengerID", Quant ,AggOps.Count, axis=Axis(title="Passengers")).
    show

<iframe id="frame-vegas-42b4618f-4933-4fe4-a84b-e01ca4e0fada" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-42b4618f-4933-4fe4-a84b-e01ca4e0fada'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "scale" : {
 "bandSize" : 20.0
 },
 "field" : "age",
 "type" : "nominal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 }
 },
 "description" : "Age Distribution of all Passengers",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Saundercock, Mr. Willi

In [10]:
Vegas("Age Distribution splitted by Survival").
    withData(train).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("age", Quant, bin=Bin(step=10.0,min= 0.0),axis=Axis(title="Age")).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-96db8688-277e-4224-9ef6-38867fce658c" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-96db8688-277e-4224-9ef6-38867fce658c'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "axis" : {
 "title" : "Age"
 },
 "field" : "age",
 "type" : "quantitative",
 "bin" : {
 "min" : 0.0,
 "step" : 10.0
 }
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Age Distribution splitted by Survival",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783"

In [11]:
Vegas("Age Distribution splitted by Survival").
    withData(train).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    addTransform("Age Description", "datum.age <= 4 ? \"1-Infant\" : datum.age<=15 ? \"2-Child\" : datum.age<=50 ? \"3-Adult\" : \"4-Old\"").
    mark(Bar).
    encodeX("Age Description", Ordinal).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-63643ea0-f281-4d4e-abb6-2aef50b5a110" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-63643ea0-f281-4d4e-abb6-2aef50b5a110'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "Age Description",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Age Distribution splitted by Survival",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass"

In [12]:
Vegas("Survival split by age").
    withData(train).
    mark(Bar).
    addTransformCalculation("age", "datum.age-(datum.age % 10)").
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeX("age", Nominal, scale = Scale(bandSize = 20.0)).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-5dd8abbd-856f-49b5-a549-cf7b021906f9" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-5dd8abbd-856f-49b5-a549-cf7b021906f9'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "scale" : {
 "bandSize" : 20.0
 },
 "field" : "age",
 "type" : "nominal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Survival split by age",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 

In [12]:
// could be intresting, maybe survival is higher when cabin close to rescue boats
// https://www.encyclopedia-titanica.org/cabins.html
// to many missing values

//Vegas("Survival by cabin").
//    withData(train).
//    mark(Bar).
//    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
//    addTransformCalculation("cabin", "(datum.cabin").
//    encodeX("cabin", Nominal, scale = Scale(bandSize = 20.0)).
//    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
//    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
//    show

In [13]:
Vegas("Survival split by embarked").
    withData(train).
    mark(Bar).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeX("embarked", Nominal, scale = Scale(bandSize = 20.0)).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-b80e9f6c-07b1-4b04-931f-2324a91218b9" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-b80e9f6c-07b1-4b04-931f-2324a91218b9'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "scale" : {
 "bandSize" : 20.0
 },
 "field" : "embarked",
 "type" : "nominal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Survival split by embarked",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerI

In [14]:
//fare (cost for ticket)
val nrClasses = 3
val sorted_train = train.filter(x => x.get("fare")!=None).sortBy(x=>x("fare").asInstanceOf[Float])
val sizeSet = sorted_train.size
val sizeIntervals = sizeSet/nrClasses
val intervals = for (x <- 1 to nrClasses-1) yield sorted_train(x*sizeIntervals)("fare").asInstanceOf[Float]
val new_Train= for(pass <- sorted_train) 
    yield pass.updated("fareclass",intervals.count(_ < pass("fare").asInstanceOf[Float]))
Vegas("Fare Distribution splitted by Calculated Intervals").
    withData(new_Train).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("fareclass", Ord).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-52623283-7377-4018-9180-5848541a1245" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-52623283-7377-4018-9180-5848541a1245'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "fareclass",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Fare Distribution splitted by Calculated Intervals",
 "data" : {
 "values" : [
 {
 "name" : "Leonard, Mr. Lionel",
 "fare" : 0.0,
 "parch" : 0,
 "age" : 36.0,
 "ticket" : "LINE",
 "sex" : "male",
 "passengerID" : 180,
 "pclass" : 3,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Harrison, Mr. William",
 "fare" : 0.0,
 "parch" : 0,
 "age" : 40.0,
 "ticket" : "112059",
 "cabin" : "B94",
 "sex" : "male",
 "passengerID" : 264,
 "pclass" : 1,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Tornquist, Mr. William Henry",
 "fare" : 0.0,
 "parch" : 0,
 "age" : 25.0,
 "ticket" : "LINE",
 "sex" : "male",
 "passengerID" : 272,
 "pclass" : 3,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Parkes, Mr. Francis \"\"Frank\"\"",
 "fare" : 0.0,
 "parch" : 0,
 "ticket" : "239853",
 "sex" : "male",
 "passengerID" : 278,
 "pclass" : 2,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mr. William Cahoone Jr",
 "fare" : 0.0,
 "parch" : 0,
 "age" : 19.0,
 "ticket" : "LINE",
 "sex" : "male",
 "passengerID" : 303,
 "pclass" : 3,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cunningham, Mr. Alfred Fleming",
 "fare" : 0.0,
 "parch" : 0,
 "ticket" : "239853",
 "sex" : "male",
 "passengerID" : 414,
 "pclass" : 2,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Campbell, Mr. William",
 "fare" : 0.0,
 "parch" : 0,
 "ticket" : "239853",
 "sex" : "male",
 "passengerID" : 467,
 "pclass" : 2,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Frost, Mr. Anthony Wood \"\"Archie\"\"",
 "fare" : 0.0,
 "parch" : 0,
 "ticket" : "239854",
 "sex" : "male",
 "passengerID" : 482,
 "pclass" : 2,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mr. Alfred",
 "fare" : 0.0,
 "parch" : 0,
 "age" : 49.0,
 "ticket" : "LINE",
 "sex" : "male",
 "passengerID" : 598,
 "pclass" : 3,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Parr, Mr. William Henry Marsh",
 "fare" : 0.0,
 "parch" : 0,
 "ticket" : "112052",
 "sex" : "male",
 "passengerID" : 634,
 "pclass" : 1,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Watson, Mr. Ennis Hastings",
 "fare" : 0.0,
 "parch" : 0,
 "ticket" : "239856",
 "sex" : "male",
 "passengerID" : 675,
 "pclass" : 2,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Knight, Mr. Robert J",
 "fare" : 0.0,
 "parch" : 0,
 "ticket" : "239855",
 "sex" : "male",
 "passengerID" : 733,
 "pclass" : 2,
 "sibsp" : 0,
 "fareclass" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Andrews, Mr. Thomas Jr",
 "fare" : 0.0,
 "parch" : 0,
 "age" : 39.0,
 "ticket" : "112050",
 "

nrClasses: Int = 3
sorted_train: List[Map[String, Any]] = List(
  Map(
    "name" -> "Leonard, Mr. Lionel",
    "fare" -> 0.0F,
    "parch" -> 0,
    "age" -> 36.0F,
    "ticket" -> "LINE",
    "sex" -> "male",
    "passengerID" -> 180,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "name" -> "Harrison, Mr. William",
    "fare" -> 0.0F,
    "parch" -> 0,
    "age" -> 40.0F,
    "ticket" -> "112059",
    "cabin" -> "B94",
    "sex" -> "male",
    "passengerID" -> 264,
    "pclass" -> 1,
    "sibsp" -> 0,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "name" -> "Tornquist, Mr. William Henry",
    "fare" -> 0.0F,
    "parch" -> 0,
    "age" -> 25.0F,
    "ticket" -> "LINE",
    "sex" -> "male",
    "passengerID" -> 272,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'S',
...
sizeSet: Int = 891
sizeIntervals: Int = 297
intervals: collection.immutable.IndexedSeq[Float] = Vector(8.6625F, 26.0F)
new_Train: List[Map[String, A

In [15]:
Vegas("pclass Distribution splitted by Calculated Intervals").
    withData(train).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("pclass", Ord).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-a5f26af2-bbdf-46c6-abc8-7cdae1c6e452" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-a5f26af2-bbdf-46c6-abc8-7cdae1c6e452'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "pclass",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "pclass Distribution splitted by Calculated Intervals",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "p

In [16]:
Vegas("number of Siblings Distribution splitted by Calculated Intervals").
    withData(train).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("sibsp", Ord).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-643cf0c5-f1be-4fa6-8cc8-34e872684d28" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-643cf0c5-f1be-4fa6-8cc8-34e872684d28'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "sibsp",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "number of Siblings Distribution splitted by Calculated Intervals",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID

In [17]:
Vegas("number of parents/children Distribution splitted by Calculated Intervals").
    withData(train).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("parch", Ord).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-4263b6eb-b423-424e-9c47-3b4af5eb90ba" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-4263b6eb-b423-424e-9c47-3b4af5eb90ba'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "parch",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "number of parents/children Distribution splitted by Calculated Intervals",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "pas

#  DATA PREPARATION

Name, Cabin & Ticket are deleted from the dataset

In [18]:

def data_preparation(data:List[Map[String,Any]]):List[Map[String,Any]]={
    // drop name, cabin, ticket
    val a = data.map(passenger => passenger.-("name"))
    val b = a.map(passenger => passenger.-("cabin"))
    val c = b.map(passenger => passenger.-("ticket"))
    // add random age to the missing values
    val r = scala.util.Random
    val train_age = train.filter(passenger => passenger.contains("age")).map(x => x("age").asInstanceOf[Float])
    val train_avg_age = c.map(passenger => 
                              if (!passenger.contains("age")) {
                                (passenger.+("age" -> r.nextInt(80).asInstanceOf[Float]))
                            }else{
                                passenger
                             })
    // add 2 values freely (Q), because only 2 missing values
    val train_embarked = train_avg_age.map(passenger => if (!passenger.contains("embarked")){
        (passenger.+("embarked" -> 'Q'))
    }else{
        passenger
    })
    val train_2 = train_embarked
    train_2
}

val t = data_preparation(train)


// drop passengerID, because no relevant information
val train_no_id = t.map(passenger => passenger.-("passengerID"))

defined function data_preparation
t: List[Map[String, Any]] = List(
  Map(
    "fare" -> 7.25F,
    "parch" -> 0,
    "age" -> 22.0F,
    "sex" -> "male",
    "passengerID" -> 1,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "fare" -> 71.2833F,
    "parch" -> 0,
    "age" -> 38.0F,
    "sex" -> "female",
    "passengerID" -> 2,
    "pclass" -> 1,
    "sibsp" -> 1,
    "embarked" -> 'C',
    "survived" -> 1
  ),
  Map(
    "fare" -> 7.925F,
    "parch" -> 0,
    "age" -> 26.0F,
    "sex" -> "female",
    "passengerID" -> 3,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'S',
    "survived" -> 1
  ),
  Map(
    "fare" -> 53.1F,
    "parch" -> 0,
    "age" -> 35.0F,
    "sex" -> "female",
...
train_no_id: List[Map[String, Any]] = List(
  Map(
    "fare" -> 7.25F,
    "parch" -> 0,
    "age" -> 22.0F,
    "sex" -> "male",
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "fare" -> 71.283

transform every attribute to categorical attributes


Age -> into 4 classes
    infant=0 => (age <= 4)
    child=1  => (age <= 15)
    adult=2  => (age <= 50)
    old=3    => (age > 50)
    
    
fare (costs) -> into 3 classes

In [19]:
def categorize_data(data:List[Map[String,Any]]):List[Map[String,Any]]={
    // fare
    val nrClasses = 3
    val sorted_train = data.sortBy(x => x("fare").asInstanceOf[Float])
    val sizeSet = sorted_train.size
    val sizeIntervals = sizeSet/nrClasses
    val intervals = for (x <- 1 to nrClasses-1) yield sorted_train(x*sizeIntervals)("fare").asInstanceOf[Float]
    val new_Train= for(pass <- sorted_train) yield pass.updated("fareClass",intervals.count(_ < pass("fare").asInstanceOf[Float]))
    
    // age
    val new_Train_2 = for(passenger <- new_Train) yield passenger.updated("ageClass", passenger("age").asInstanceOf[Float] match {
      case x if (x <= 4) => 0
      case x if (x > 4) && (x <= 15) => 1
      case x if (x > 15) && (x <= 50) => 2
      case x if (x > 50) => 3
      case _ => -1
    })
    
    //drop the fare & age feature, because categorized into fareClass & ageClass
    val train_no_fare = new_Train_2.map(passenger => passenger.-("fare"))
    val train_no_age = train_no_fare.map(passenger => passenger.-("age"))
    val train_final = train_no_age
    train_final
}

val train_final = categorize_data(train_no_id)

defined function categorize_data
train_final: List[Map[String, Any]] = List(
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "pclass" -> 3,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "pclass" -> 1,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "pclass" -> 3,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> 1
  ),
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "pclass" -> 2,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
...

# NAIVE BAYES IMPLEMENTATION

In [20]:
val data_passengers_survived = train_final.filter(passenger => passenger("survived").equals(1))
val data_passengers_not_survived = train_final.filter(passenger => passenger("survived").equals(0))

data_passengers_survived: List[Map[String, Any]] = List(
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "pclass" -> 3,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> 1
  ),
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "pclass" -> 3,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> 1
  ),
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "pclass" -> 3,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> 1
  ),
  Map(
    "parch" -> 0,
    "sex" -> "female",
    "ageClass" -> 1,
    "pclass" -> 3,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'C',
...
data_passengers_not_survived: List[Map[String, Any]] = List(
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "pclass" -> 3,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "parch" -> 0,
    "s

In [21]:
def count_occurrence_of_att(data:List[Map[String,Any]]):Map[(String,Any),Int] = {
    data.flatten.groupBy(identity).mapValues(_.size)
}

val occ_survived = count_occurrence_of_att(data_passengers_survived)
val occ_not_survived = count_occurrence_of_att(data_passengers_not_survived)

defined function count_occurrence_of_att
occ_survived: Map[(String, Any), Int] = Map(
  ("sex", "male") -> 109,
  ("survived", 1) -> 342,
  ("sibsp", 1) -> 112,
  ("embarked", 'C') -> 93,
  ("parch", 5) -> 1,
  ("sibsp", 2) -> 13,
  ("fareClass", 2) -> 165,
  ("embarked", 'S') -> 217,
  ("parch", 3) -> 3,
  ("ageClass", 2) -> 244,
  ("ageClass", 3) -> 36,
  ("pclass", 2) -> 87,
  ("parch", 2) -> 40,
  ("sibsp", 3) -> 4,
  ("ageClass", 1) -> 33,
  ("pclass", 1) -> 136,
  ("ageClass", 0) -> 29,
  ("sex", "female") -> 233,
  ("pclass", 3) -> 119,
  ("sibsp", 0) -> 210,
  ("fareClass", 0) -> 61,
  ("parch", 0) -> 233,
  ("fareClass", 1) -> 116,
  ("sibsp", 4) -> 3,
  ("embarked", 'Q') -> 32,
  ("parch", 1) -> 65
)
occ_not_survived: Map[(String, Any), Int] = Map(
  ("sex", "male") -> 468,
  ("sibsp", 1) -> 97,
  ("embarked", 'C') -> 75,
  ("parch", 5) -> 4,
  ("sibsp", 2) -> 15,
  ("fareClass", 2) -> 130,
  ("embarked", 'S') -> 427,
  ("parch", 3) -> 2,
  ("ageClass", 2) -> 404,
  ("sibsp",

Creating 2 maps (for class survived & not survived) containing the conditional probabilities

In [22]:
// helper get the number of different values for specific attribute
// ex: attribute pclass has 3 different values 
def getNbOfDiffValuesOfAttr(data:List[Map[String,Any]],att:String):Int = {
    data.map(passenger => passenger(att)).distinct.size
}


// smoothing
// conditional probability of each attribute
// p(att)=(#(d^c)+1)/(#(c)+m) with m = nb of different attribute values
def conditional_prob_of_att(occ:Map[(String,Any),Int],survived:Int):Map[(String,Any),Double]= {
      occ.map(x 
              => 
              ((x._1._1,x._1._2), ((x._2+1)/(occ("survived",survived)+getNbOfDiffValuesOfAttr(train_final,x._1._1)).asInstanceOf[Double])))
}

val prob_survived = conditional_prob_of_att(occ_survived,1)
val prob_not_survived = conditional_prob_of_att(occ_not_survived,0)

defined function getNbOfDiffValuesOfAttr
defined function conditional_prob_of_att
prob_survived: Map[(String, Any), Double] = Map(
  ("sex", "male") -> 0.31976744186046513,
  ("survived", 1) -> 0.997093023255814,
  ("sibsp", 1) -> 0.3237822349570201,
  ("embarked", 'C') -> 0.27246376811594203,
  ("parch", 5) -> 0.0057306590257879654,
  ("sibsp", 2) -> 0.04011461318051576,
  ("fareClass", 2) -> 0.4811594202898551,
  ("embarked", 'S') -> 0.6318840579710145,
  ("parch", 3) -> 0.011461318051575931,
  ("ageClass", 2) -> 0.708092485549133,
  ("ageClass", 3) -> 0.1069364161849711,
  ("pclass", 2) -> 0.25507246376811593,
  ("parch", 2) -> 0.1174785100286533,
  ("sibsp", 3) -> 0.014326647564469915,
  ("ageClass", 1) -> 0.09826589595375723,
  ("pclass", 1) -> 0.39710144927536234,
  ("ageClass", 0) -> 0.08670520231213873,
  ("sex", "female") -> 0.6802325581395349,
  ("pclass", 3) -> 0.34782608695652173,
  ("sibsp", 0) -> 0.6045845272206304,
  ("fareClass", 0) -> 0.17971014492753623,
  ("parch", 0

# PREDICTION

TestData preparation

Check for missing values

In [23]:
val missing_values = countAllMissingValues(test,attList)

missing_values: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 1,
  "parch" -> 0,
  "age" -> 86,
  "ticket" -> 0,
  "cabin" -> 327,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 0,
  "survived" -> 0
)

Add missing value fare manually (only 1 missing value)

In [24]:
val test_1 = test.map(passenger => 
                      if (!passenger.contains("fare")){
                        (passenger.+("fare" -> 12.5F))
                    }else{
                        passenger
                    })

test_1: List[Map[String, Any]] = List(
  Map(
    "name" -> "Kelly, Mr. James",
    "fare" -> 7.8292F,
    "parch" -> 0,
    "age" -> 34.5F,
    "ticket" -> "330911",
    "sex" -> "male",
    "passengerID" -> 892,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'Q',
    "survived" -> -1
  ),
  Map(
    "name" -> "Wilkes, Mrs. James (Ellen Needs)",
    "fare" -> 7.0F,
    "parch" -> 0,
    "age" -> 47.0F,
    "ticket" -> "363272",
    "sex" -> "female",
    "passengerID" -> 893,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> -1
  ),
  Map(
    "name" -> "Myles, Mr. Thomas Francis",
    "fare" -> 9.6875F,
    "parch" -> 0,
    "age" -> 62.0F,
    "ticket" -> "240276",
    "sex" -> "male",
    "passengerID" -> 894,
    "pclass" -> 2,
    "sibsp" -> 0,
    "embarked" -> 'Q',
    "survived" -> -1
...

In [25]:
val test_data = data_preparation(test_1)

test_data: List[Map[String, Any]] = List(
  Map(
    "fare" -> 7.8292F,
    "parch" -> 0,
    "age" -> 34.5F,
    "sex" -> "male",
    "passengerID" -> 892,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'Q',
    "survived" -> -1
  ),
  Map(
    "fare" -> 7.0F,
    "parch" -> 0,
    "age" -> 47.0F,
    "sex" -> "female",
    "passengerID" -> 893,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> -1
  ),
  Map(
    "fare" -> 9.6875F,
    "parch" -> 0,
    "age" -> 62.0F,
    "sex" -> "male",
    "passengerID" -> 894,
    "pclass" -> 2,
    "sibsp" -> 0,
    "embarked" -> 'Q',
    "survived" -> -1
  ),
  Map(
    "fare" -> 8.6625F,
    "parch" -> 0,
    "age" -> 27.0F,
    "sex" -> "male",
...

Change the data to only categorical 

In [26]:
val data_test_2 = categorize_data(test_data)

data_test_2: List[Map[String, Any]] = List(
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "passengerID" -> 1158,
    "pclass" -> 1,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> -1
  ),
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "passengerID" -> 1264,
    "pclass" -> 1,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> -1
  ),
  Map(
    "parch" -> 1,
    "sex" -> "male",
    "ageClass" -> 1,
    "passengerID" -> 913,
    "pclass" -> 3,
    "sibsp" -> 0,
    "fareClass" -> 0,
    "embarked" -> 'S',
    "survived" -> -1
  ),
  Map(
    "parch" -> 0,
    "sex" -> "male",
    "ageClass" -> 2,
    "passengerID" -> 1008,
...

In [27]:
def predict_for_passenger(prob_survived:Map[(String, Any), Double],
                            prob_not_survived:Map[(String, Any), Double],
                            passenger:Map[String,Any]):(Int,Int) = {
    val passenger_id  = passenger("passengerID").asInstanceOf[Int]
    val data_size = prob_survived.size.asInstanceOf[Double] + prob_not_survived.size.asInstanceOf[Double]
    val prior_prob_survived = (prob_survived.size/data_size).asInstanceOf[Double]
    val prior_prob_not_survived = (prob_not_survived.size/data_size).asInstanceOf[Double]
    
    // only probabilities relevant for passenger (class survived)
    val tmp_prob_survived = prob_survived.filter(x => x._1._2.equals(passenger(x._1._1))).
        values.map(x=>scala.math.log(x))
    // only probabilities relevant for passenger (class not survived)
    val tmp_prob_not_survived = prob_not_survived.filter(x => x._1._2.equals(passenger(x._1._1))).
        values.map(x=>scala.math.log(x))
    
    val res_survived = scala.math.log(prior_prob_survived) + tmp_prob_survived.foldLeft(0.0)(_+_)
    val res_not_survived = scala.math.log(prior_prob_not_survived) + tmp_prob_not_survived.foldLeft(0.0)(_+_)
    if(res_survived > res_not_survived){
        (passenger_id,1)
    }else{
        (passenger_id,0)
    }
}

defined function predict_for_passenger

In [28]:
// prediction Seq[(ID,CLASS)]
// ID of passenger
// Class => predicted class for passenger (survived/not survived)
def predict(prob_survived:Map[(String, Any), Double],
            prob_not_survived:Map[(String, Any), Double],
            test_data:List[Map[String,Any]]):Seq[(Int,Int)] = {
    test_data.map(passenger => predict_for_passenger(prob_survived,prob_not_survived,passenger))
}

defined function predict

In [29]:
val prediction_for_test_data = predict(prob_survived,prob_not_survived,data_test_2)

prediction_for_test_data: Seq[(Int, Int)] = List(
  (1158, 0),
  (1264, 0),
  (913, 0),
  (1008, 0),
  (1025, 0),
  (1124, 0),
  (1183, 0),
  (893, 0),
  (1055, 0),
  (1103, 0),
  (1217, 0),
  (909, 0),
  (911, 1),
  (919, 0),
  (1028, 0),
  (1063, 0),
  (1129, 0),
  (1166, 0),
  (1203, 0),
  (1224, 0),
  (900, 1),
  (927, 0),
  (1065, 0),
  (1180, 0),
  (1184, 0),
  (1213, 0),
  (1229, 0),
  (1231, 0),
  (1239, 1),
  (1015, 0),
  (1177, 0),
  (1178, 0),
  (1288, 0),
  (1307, 0),
  (1005, 0),
  (1047, 0),
  (1062, 0),
  (1147, 0),
...

In [58]:
// submit file for kaggle
def createSubmitFile[ID, CLASS](filename: String, data: Seq[(ID, CLASS)], header: String): Unit = {
    val pw = new PrintWriter(filename)
    pw.println(header)
    data.foreach(e => pw.println(e._1.toString + "," + e._2.toString))
    pw.close()
  }

createSubmitFile("mySubmission.csv",prediction_for_test_data,"PassengerId,Survived")

defined function createSubmitFile